In [70]:
!pyspark --version

Welcome to
      ____              __
     / __/__  ___ _____/ /__
    _\ \/ _ \/ _ `/ __/  '_/
   /___/ .__/\_,_/_/ /_/\_\   version 2.4.1
      /_/
                        
Using Scala version 2.11.12, Java HotSpot(TM) 64-Bit Server VM, 1.8.0_202
Branch 
Compiled by user  on 2019-03-26T22:44:44Z
Revision 
Url 
Type --help for more information.


In [9]:
!python --version

Python 3.7.3


In [8]:
!pip install pyspark

In [1]:
from nest_recom_spark_session import nest_get_spark_session
obj=nest_get_spark_session()

sc,sqlContext = obj.start_or_get_spark(
					app_name="NestReadyRecommendationEngine", 
					url='local[2]',
					memory="20g"
					)

In [64]:





#paths=['/Users/jatinmalhotra/Desktop/not2/one/*','/Users/jatinmalhotra/Desktop/not2/two/*']


#df=sqlContext.read.json(*paths) 

# * can be files or directories

df = sqlContext.read.options(header='false', inferschema='true').json('/Users/jatinmalhotra/Desktop/not/')





In [61]:
df.write.mode("append").saveAsTable(l_table_name)

In [134]:
sqlContext.sql("SELECT 1 FROM {} where 1=2".format(l_table_name)).show()


+---+
|  1|
+---+
+---+



In [125]:
df.write.mode("append").saveAsTable("hello")

In [132]:
sqlContext.sql("select * from hello where 1=2").show()

+---------+-----------+--------+-------+-------+-----+---------+----+-----------------+---------+----------+----------+------+---------+----+------+-------+--------+
|_metadata|anonymousId|category|channel|context|event|messageId|name|originalTimestamp|projectId|properties|receivedAt|sentAt|timestamp|type|userId|version|writeKey|
+---------+-----------+--------+-------+-------+-----+---------+----+-----------------+---------+----------+----------+------+---------+----+------+-------+--------+
+---------+-----------+--------+-------+-------+-----+---------+----+-----------------+---------+----------+----------+------+---------+----+------+-------+--------+



In [124]:
sqlContext.sql("SELECT a.* from df_tmp a where 1=1 and exists (select 1 from {} where a.messageId=messageId)".format(l_table_name)).show()




+--------------------+--------------------+--------+-------+--------------------+-----+--------------------+----+--------------------+----------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+-------+--------------------+
|           _metadata|         anonymousId|category|channel|             context|event|           messageId|name|   originalTimestamp| projectId|          properties|          receivedAt|              sentAt|           timestamp| type|              userId|version|            writeKey|
+--------------------+--------------------+--------+-------+--------------------+-----+--------------------+----+--------------------+----------+--------------------+--------------------+--------------------+--------------------+-----+--------------------+-------+--------------------+
|[[Google Analytic...|1563da5c-53da-452...|    null| client|[99.226.176.165, ...| null|ajs-0cb17c494b79b...|Home|2019-03-29T17:49:...|JSmm0eow

+---+
|  1|
+---+
|  1|
|  1|
+---+



In [58]:
df.count()

2

In [22]:
df.registerTempTable("sql_table")

In [31]:
sqlContext.sql("select messageId from sql_table a where 1=1 and not exists (select 1 from sql_table b where a.messageId=b.messageId)").show()







+---------+
|messageId|
+---------+
+---------+



In [32]:
sqlContext.sql("select messageId, count(1) from sql_table group by messageId having count(1)>1").show()







+--------------------+--------+
|           messageId|count(1)|
+--------------------+--------+
|ajs-b84b19756fb73...|       2|
+--------------------+--------+



In [157]:
sqlContext.sql("select event, count(*) from sql_table where properties.category is NULL group by event").show()

+------------------+--------+
|             event|count(1)|
+------------------+--------+
|     has_scheduled|       1|
|   prop-page-email|       3|
|              null|    8980|
|      has_favorite|       5|
|exitEmailSubmitted|       6|
|     proceedNoSave|      23|
|                BE|  122837|
|    Update Contact|      67|
|            Search|    2496|
+------------------+--------+



In [77]:
df.select("event").distinct().count()


225

In [78]:
df.rdd.getNumPartitions()

4485

In [79]:
print(df.rdd.partitioner)

None


In [80]:
df.rdd.partitions.size()

AttributeError: 'RDD' object has no attribute 'partitions'

In [81]:
df.count()

143511

In [82]:
df.printSchema()

root
 |-- _metadata: struct (nullable = true)
 |    |-- bundled: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- unbundled: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |-- anonymousId: string (nullable = true)
 |-- category: string (nullable = true)
 |-- channel: string (nullable = true)
 |-- context: struct (nullable = true)
 |    |-- campaign: struct (nullable = true)
 |    |    |-- content: string (nullable = true)
 |    |    |-- medium: string (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- source: string (nullable = true)
 |    |-- ip: string (nullable = true)
 |    |-- library: struct (nullable = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- version: string (nullable = true)
 |    |-- page: struct (nullable = true)
 |    |    |-- path: string (nullable = true)
 |    |    |-- referrer: string (nullable = true)
 |    |    |-- search: string (nullable = true)


In [83]:
import sys
print("System version: {}".format(sys.version))
sc.sparkContext._conf.getAll()

System version: 3.7.3 (default, Mar 27 2019, 16:54:48) 
[Clang 4.0.1 (tags/RELEASE_401/final)]


[('spark.driver.memory', '32g'),
 ('spark.rdd.compress', 'True'),
 ('spark.serializer.objectStreamReset', '100'),
 ('spark.executor.id', 'driver'),
 ('spark.submit.deployMode', 'client'),
 ('spark.app.name', 'NestReadyRecommendationEngine'),
 ('spark.driver.port', '51616'),
 ('spark.ui.showConsoleProgress', 'true'),
 ('spark.master', 'local[2]'),
 ('spark.driver.host', '192.168.1.108'),
 ('spark.app.id', 'local-1555348143731')]

In [30]:
sqlContext.sql("select userId, substr(context.page.path,11,length(context.page.path)) as propertyId, event as weight from table where userId is not null and event in ('ScheduleVisit','Unfavorited','PhotoClicked','CalculateClicked','MortgageCalculatorCTAClicked','ContactPartnerClicked','RequestInformationClicked','SimilarPropertyClicked','PartnerBanner','MapPinClicked','CallClicked','Prop-page-email','ChatClicked','AgentCall','AgentEmail','ComponentTriggered') order by userId").show()


+------+----------+------+
|userId|propertyId|weight|
+------+----------+------+
+------+----------+------+



In [1]:

from nest_recom_spark_session import nest_get_spark_session

# Load Json to spark dataframe
from nest_recom_loader import load_spark_df

from nest_recom_event_mapper import (
	map_weights, 
	numeric_conversion
)

from nest_recom_constants import (
	FILE_PATH, 
	NUM_RECOM_PER_USR
	)

from nest_recom_als_model import nest_recom_als


def set_spark_local():
	obj=nest_get_spark_session()

	sc,sqlContext = obj.start_or_get_spark(
					app_name="NestReadyRecommendationEngine", 
					url='local[2]',
					memory="20g"
					)
	return sc, sqlContext


def set_spark_prod():
	sqlContext=SQLContext(sc)
	return sqlContext


sc,sqlContext = set_spark_local()

#sqlContext = set_spark_prod()



data=load_spark_df(sqlContext,FILE_PATH)

#print(data.count())


df = map_weights(data,sc,sqlContext)

df1 = numeric_conversion(df)


# popularity matrix
#popularity_df = popularity_matrix(df1)
#popularity_df.show()


# COllaborative Filtering (User Behaviour )
nest_recom_als=nest_recom_als()
model=nest_recom_als.als_algo(df1)


#als_df=nest_recom_als.recommend(NUM_RECOM_PER_USR,model,df1)


#als_df.show()

In [ ]:
import org.apache.spark.ml.regression.LinearRegression
import org.apache.spark.ml.PipelineModel
val lr = new LinearRegression().setLabelCol("labesl").setFeaturesCol("features").setMaxIter(10).setRegParam(1.0).setElasticNetParam(1.0)

val pipeline = new Pipeline().setStages(Array(lr))

pipeline.fit(trainingData)

pipeline.write.overwrite().save("hdfs://.../spark/mllib/models/linearRegression");

val sameModel = PipelineModel.load("hdfs://...")

sameModel.transform(assembler).select("features", "labels", "prediction").show(

In [23]:
from pyspark.ml.recommendation import ALS
model1 = model.write()

In [17]:
model

ALS_efe3439f64d7

In [11]:
a=model.load("nest_recom_trained_model2")

In [6]:
userRecs = a.recommendForAllUsers(5)

In [8]:
# Generate top 10 movie recommendations for each user
user85Recs = userRecs.filter(userRecs['new_userId'] == 17611).collect()

for row in user85Recs:
    for rec in row.recommendations:
        print(rec.new_propertyId,rec.rating)
            

In [2]:
model.write().overwrite().save("nest_recom_trained_model")
from pyspark.ml.recommendation import ALSModel
h=ALSModel.load("nest_recom_trained_model")

In [35]:
from pyspark.ml.recommendation import ALSModel
h=ALSModel.load("nest_recom_trained_model")

In [36]:
userRecs = h.recommendForAllUsers(5)

In [39]:
user85Recs = userRecs.filter(userRecs['new_userId'] == 176).collect()

for row in user85Recs:
    for rec in row.recommendations:
        print(rec.new_propertyId,rec.rating)
            

290 29.98984146118164
47 19.90692710876465
167 17.0316219329834
503 15.542365074157715
465 13.806079864501953


In [123]:
from sklearn.externals import joblib

models = joblib.load('nest_recom_trained_model/')

IsADirectoryError: [Errno 21] Is a directory: 'nest_recom_trained_model/'

In [159]:
from pyspark.mllib.recommendation import ALS, MatrixFactorizationModel, Rating
from pyspark.mllib.tree import RandomForest, RandomForestModel

sameModel = RandomForestModel.load(sc,⁨"nest_recom_trained_model")

SyntaxError: invalid character in identifier (<ipython-input-159-260880a1773f>, line 4)

SyntaxError: invalid character in identifier (<ipython-input-144-810a7c93ef08>, line 5)

In [113]:
from pyspark.mllib.recommendation import ALS, MatrixFactorizationModel, Rating
model_1 = MatrixFactorizationModel.load("nest_recom_trained_model")


TypeError: load() missing 1 required positional argument: 'path'

In [84]:

# Name: - nest_event_mapping_json
# Input:- events weight mapping json object
# Description: - Function event weights mapping json object as a table to join with main table
# calling :- df=nest_event_mapping_json("eventmapping.json")
def nest_event_mapping_json(file_name):
    event_mapping=sqlContext.read.json(file_name)
    event_mapping.registerTempTable("event_mapping_table")
    df=sqlContext.sql("select a.userId, substr(context.page.path,11,length(context.page.path)) as propertyId, a.event, e.weight from table a, event_mapping_table e where a.userId is not null and a.event=e.event order by a.userId")
    return df



# Name: - nest_event_mapping_replace
# Input:- events weight mapping using replace function
# Description: - Function to apply event weights mapping
# calling :- df=nest_event_mapping_replace("df")
def nest_event_mapping_replace(data,sc,sqlContext):
    
    data.registerTempTable("table")

    df=sqlContext.sql("select userId, substr(context.page.path,11,length(context.page.path)) as propertyId, event as weight from table where userId is not null and event in ('ScheduleVisit','Unfavorited','PhotoClicked','CalculateClicked','MortgageCalculatorCTAClicked','ContactPartnerClicked','RequestInformationClicked','SimilarPropertyClicked','PartnerBanner','MapPinClicked','CallClicked','Prop-page-email','ChatClicked','AgentCall','AgentEmail','ComponentTriggered') order by userId")
    
    #file_name="UserEvents/events_mapping.json"
    #events_mapping=sqlContext.read.json(file_name)
    EVENTS_MAPPING={"Favorited":"10",
                    "PartnerCTAClicked":"20",
                    "ScheduleVisit":"30",
                    "proceedNoSave":"35",
                    "PriceClicked":"5",
                    "ThumbnailClicked":"5",
                    "LocaleClicked":"5",
                    "Unfavorited":"-10",
                    "PhotoClicked":"10",
                    "CalculateClicked":"10",
                    "MortgageCalculatorCTAClicked":"10",
                    "ContactPartnerClicked":"20",
                    "RequestInformationClicked":"20",
                    "SimilarPropertyClicked":"5",
                    "PartnerBanner":"10",
                    "MapPinClicked":"5",
                    "CallClicked":"40",
                    "Prop-page-email":"40",
                    "ChatClicked":"40",
                    "AgentCall":"45",
                    "AgentEmail":"45",
                    "CashbackClicked":"10",
                    "StickyContactButton":"30",
                    "StickyCall":"30",
                    "StickyGetinTouch":"30",
                    "StickyChat":"30",
                    "ComponentTriggered":"30",
                    "GetURLClicked":"5",
                    "OTHERS":"10"
                    }
    
    df2 = df.replace(to_replace=EVENTS_MAPPING, subset=['weight'])
    
    df3 = df2.groupBy("userId","propertyId").agg({'weight':'avg'})
    df4 = df3.withColumnRenamed('avg(weight)', 'weight')
    df5 = df4.fillna({'weight':5})
    #df6 = df5.na.drop()
    
    

    return df5


from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer
from pyspark.sql.functions import col
def nest_numeric_conversion(data):
    indexers = [StringIndexer(inputCol=column, outputCol="new_"+column).fit(data) for column in list(set(data.columns)-set(['weight'])) ]
    pipeline = Pipeline(stages=indexers)
    df_r = pipeline.fit(data).transform(data)
    
    df_r = df_r.withColumn("new_userId", col("new_userId").cast("int"))
    df_r = df_r.withColumn("new_propertyId", col("new_propertyId").cast("int"))
    df_r = df_r.withColumn("weight", col("weight").cast("int"))
    
    
    ## TBD
    df_r = df_r.filter(df_r["new_propertyId"]!=0)
   
    
    return df_r
    
    '''
    stringIndexer = StringIndexer(inputCol="userId", outputCol="new_userId")
    model = stringIndexer.fit(sql_data)
    df_spark_index = model.transform(sql_data).withColumn("new_userId", col("new_userId").cast("int"))
    df_spark_index.show()
   
    # Convert artists names into numerical IDs
     data['user_id'] = data['user'].astype("category").cat.codes
     data['artist_id'] = data['artist'].astype("category").cat.codes

     # Create a lookup frame so we can get the artist names back in 
     # readable form later.
     item_lookup = data[['artist_id', 'artist']].drop_duplicates()
     item_lookup['artist_id'] = item_lookup.artist_id.astype(str)

     data = data.drop(['user', 'artist'], axis=1)

    # Drop any rows that have 0 plays
     data = data.loc[data.plays != 0]

     # Create lists of all users, artists and plays
     users = list(np.sort(data.user_id.unique()))
     artists = list(np.sort(data.artist_id.unique()))
     plays = list(data.plays)

     # Get the rows and columns for our new matrix
     rows = data.user_id.astype(int)
     cols = data.artist_id.astype(int)

     '''
    


from pyspark.ml.recommendation import ALS
import time

def als_algo(data):
    als = ALS(userCol="new_userId", itemCol="new_propertyId", ratingCol="weight",coldStartStrategy="nan")
    #start_time = time.time()
    model = als.fit(data)
    #train_time = time.time() - start_time
    #print("Took {} seconds for training.".format(train_time))
    return model


from pyspark.sql import SQLContext,functions as F
def recommend(n,model,df2):
    userRecs = model.recommendForAllUsers(n)
    
    aa=userRecs.withColumn("recommendations",F.explode("recommendations"))
    aa=aa.select("new_userId","recommendations.new_propertyId","recommendations.rating")
    
    #aa_joined = aa.join(df2,['new_userId','new_propertyId'],'inner')
    aa_joined = aa.join(df2,['new_userId','new_propertyId'])

    #df = df1.join(df2, (df1.x1 == df2.x1) & (df1.x2 == df2.x2))
    return aa_joined
    


##########
## MAIN ##
##########

# Set Spark Session\n",
# the following settings work well for debugging locally on VM - change when running on a cluster\n",
# set up a giant single executor with many threads and specify memory cap\n",
from nest_recom_spark_session import start_or_get_spark
sc,sqlContext = start_or_get_spark("NestReadyRecommendationEngine", memory="16g")


# Load Json to spark dataframe
from nest_recom_loader import load_spark_df

FILE_PATH="/Users/jatinmalhotra/Desktop/not/"

data=load_spark_df(sqlContext,FILE_PATH)

df=nest_event_mapping_replace(data,sc,sqlContext)

df1=nest_numeric_conversion(df)

######df2.where(col("weight").isNull()).show()
df2 = df1.fillna({'weight':5})

model=als_algo(df2)

final_df=recommend(10,model,df2)



ImportError: cannot import name 'start_or_get_spark' from 'nest_recom_spark_session' (/Users/jatinmalhotra/Desktop/NestReady_Recommendation_System/CODING/nest_recommendation_engine/nest_recom_spark_session.py)

In [4]:

from nest_recom_spark_session import nest_get_spark_session

# Load Json to spark dataframe
from nest_recom_loader import load_spark_df

from nest_recom_event_mapper import (
	map_weights, 
	numeric_conversion
)

from nest_recom_constants import (
	FILE_PATH, 
	NUM_RECOM_PER_USR
	)

from nest_recom_als_model import nest_recom_als


def set_spark_local():
	obj=nest_get_spark_session()

	sc,sqlContext = obj.start_or_get_spark(
					app_name="NestReadyRecommendationEngine", 
					url='local[2]',
					memory="20g"
					)
	return sc, sqlContext


def set_spark_prod():
	sqlContext=SQLContext(sc)
	return sqlContext


sc,sqlContext = set_spark_local()

#sqlContext = set_spark_prod()



data=load_spark_df(sqlContext,FILE_PATH)

#print(data.count())


df = map_weights(data,sc,sqlContext)

df1 = numeric_conversion(df)


nest_recom_als=nest_recom_als()
model=nest_recom_als.als_algo(df1)


final_df=nest_recom_als.recommend(NUM_RECOM_PER_USR,model,df1)




final_df.show()


+--------------------+--------------------+
|              userId|     Recommendations|
+--------------------+--------------------+
|0e691f3840a8b4bd3...|[5c695e21d4c80c00...|
|27452dd2e1a70ca2f...|[5c50d7388e327600...|
|27452dd2e1a70ca2f...|[5bbe6f1c7c1e9000...|
|027f71d9d6351ec3a...|[chedule/5c96251f...|
|027f71d9d6351ec3a...|[5ca13ffb5a8dd600...|
|119e3cd34ea146edf...|[5c5bf1dd8e327600...|
|0bc2e7b1349c3d915...|[5c694d0a8e327600...|
|0bc2e7b1349c3d915...|[5c4bc8c98e327600...|
|3302b5091c9287e82...|[5c693a508e327600...|
|3302b5091c9287e82...|[5c5c32df8e327600...|
|3302b5091c9287e82...|[5c62a87f8e327600...|
|3302b5091c9287e82...|[5c6297298e327600...|
|19db47fec8cc8327f...|[5c54514bf5124b00...|
|19db47fec8cc8327f...|[5bcdd67fee13c600...|
|259c86e07b4f41e1a...|[5c78d666c5c1f100...|
|066d64b433be22261...|[chedule/5c939f23...|
|35576dffbe6a1ac9c...|[5c5ca33f8e327600...|
|35576dffbe6a1ac9c...|[5c7d8b8e92596f00...|
|20912ede5441f4c1f...|[5c82a9a2be7c7e00...|
|2fc6ab147ced058ac...|[5ca2f0d1b

In [10]:
model.

+--------------------+--------------------+
|              userId|     Recommendations|
+--------------------+--------------------+
|0e691f3840a8b4bd3...|[5c695e21d4c80c00...|
|27452dd2e1a70ca2f...|[5c50d7388e327600...|
|27452dd2e1a70ca2f...|[5bbe6f1c7c1e9000...|
|027f71d9d6351ec3a...|[chedule/5c96251f...|
|027f71d9d6351ec3a...|[5ca13ffb5a8dd600...|
|119e3cd34ea146edf...|[5c5bf1dd8e327600...|
|0bc2e7b1349c3d915...|[5c694d0a8e327600...|
|0bc2e7b1349c3d915...|[5c4bc8c98e327600...|
|3302b5091c9287e82...|[5c693a508e327600...|
|3302b5091c9287e82...|[5c5c32df8e327600...|
|3302b5091c9287e82...|[5c62a87f8e327600...|
|3302b5091c9287e82...|[5c6297298e327600...|
|19db47fec8cc8327f...|[5c54514bf5124b00...|
|19db47fec8cc8327f...|[5bcdd67fee13c600...|
|259c86e07b4f41e1a...|[5c78d666c5c1f100...|
|066d64b433be22261...|[chedule/5c939f23...|
|35576dffbe6a1ac9c...|[5c5ca33f8e327600...|
|35576dffbe6a1ac9c...|[5c7d8b8e92596f00...|
|20912ede5441f4c1f...|[5c82a9a2be7c7e00...|
|2fc6ab147ced058ac...|[5ca2f0d1b

In [11]:
printDf(final_df)

In [ ]:
#final_df.select("propertyId","Recommendations.rating").groupby("Recommendations.rating")

In [17]:
final_df.printSchema()

root
 |-- userId: string (nullable = true)
 |-- Recommendations: struct (nullable = false)
 |    |-- propertyId: string (nullable = true)
 |    |-- rating: float (nullable = true)



In [32]:
def nest_popularity_matrix(final_df):

    df3 = final_df.groupBy("Recommendations.propertyId").agg({'Recommendations.rating':'avg'})
    df4 = df3.withColumnRenamed('avg(Recommendations.rating AS `rating`)', 'avg_rating')

    df5 = df4.orderBy('avg_rating', ascending=False)


    return df5

In [69]:
final_df.cache() \
        .filter("Recommendations.rating <=10") \
        .groupBy("Recommendations.propertyId") \
        .agg({'Recommendations.rating':'avg'}) \
        .withColumnRenamed('avg(Recommendations.rating AS `rating`)', 'avg_rating') \
        .orderBy('avg_rating', ascending=False) \
        .show()
#df4 = df3.withColumnRenamed('avg(Recommendations.rating AS `rating`)', 'avg_rating')

#df5 = df4.orderBy('avg_rating', ascending=False)


+--------------------+-----------------+
|          propertyId|       avg_rating|
+--------------------+-----------------+
|5c5ca33f8e3276000...|9.996333122253418|
|5c83b101d4c80c000...| 9.99392032623291|
|5ca13ffb5a8dd6000...| 9.99392032623291|
|5c7ef7336f65df000...| 9.99392032623291|
|5c87d1a3be7c7e000...|9.989766120910645|
|5c911e83835437000...| 9.98586130142212|
|5c752d7fd4c80c000...|9.982344627380371|
|5c4c5592dc2e4d000...|9.982344627380371|
|5c6fe7c2d4c80c000...|9.978372573852539|
|5c7f5de164ad71000...|9.976850032806396|
|5ca6fcd7fe4828000...|9.976128578186035|
|5c788618c5c1f1000...|9.976128578186035|
|5c4c1ae98e3276000...|9.976128578186035|
|5c2f95dcbc09e7000...|9.970279693603516|
|5c975de87f80ae000...|9.970279693603516|
|5c4c0d518e3276000...|9.970279693603516|
|5c4c591f8e3276000...|9.970279693603516|
|5c38ab5eef84e2000...|9.970279693603516|
|5c74fce0c5c1f1000...|9.970279693603516|
|5c6955608e3276000...|9.970279693603516|
+--------------------+-----------------+
only showing top

In [ ]:
sdf1.cache() \
    .filter("month in (1, 3, 5)") \
    .groupby("month") \
    .agg(fn.mean("dep_time").alias("avg_dep"), fn.mean("arr_time").alias("avg_arr")) \

df.groupBy("group")\
  .agg({"money":"sum"})\
  .withColumnRenamed("SUM(money)", "money")
  .show(100)

In [31]:
df5.show()

+--------------------+------------------+
|          propertyId|        avg_rating|
+--------------------+------------------+
|chedule/5c9351082...|29.989843368530273|
|chedule/5b597bc3a...|29.989843368530273|
|chedule/5c880e55b...| 29.98984146118164|
|chedule/5c785e249...| 29.98984146118164|
|chedule/5c87ef90b...| 29.98984146118164|
|chedule/5c8bb974b...| 29.98984146118164|
|chedule/5c8bf4a4b...| 29.98984146118164|
|chedule/5c939f23b...| 29.98984146118164|
|chedule/5c1cf0b39...|29.989839553833008|
|chedule/5c768f3dd...|29.989839553833008|
|chedule/5c7cc7d4c...|29.989839553833008|
|chedule/5c9b9b14b...|29.989839553833008|
|chedule/5c8c7357b...|29.989839553833008|
|chedule/5c9b28287...|29.989839553833008|
|chedule/5c768ea8d...|29.989839553833008|
|5c99cb98b5d508000...|29.989839553833008|
|5c8a17d1be7c7e000...|29.989837646484375|
|chedule/5c70242d0...|29.989837646484375|
|chedule/5c545214f...|29.988361358642578|
|chedule/5c602f3fd...|29.988361358642578|
+--------------------+------------

In [22]:
df3 = final_df.groupBy("Recommendations.propertyId").agg({'Recommendations.rating':'avg'}).orderBy('avg(Recommendations.rating)', ascending=False).show()
df4 = df3.withColumnRenamed('avg(Recommendations.rating)', 'avg_rating')

    #df5 = df4.fillna({'weight':5})
    #df6 = df5.na.drop()
    

AnalysisException: "cannot resolve '`avg(Recommendations.rating)`' given input columns: [propertyId, avg(Recommendations.rating AS `rating`)];;\n'Sort ['avg(Recommendations.rating) DESC NULLS LAST], true\n+- Aggregate [Recommendations#229.propertyId], [Recommendations#229.propertyId AS propertyId#7089, avg(cast(Recommendations#229.rating as double)) AS avg(Recommendations.rating AS `rating`)#7087]\n   +- Project [userId#22, Recommendations#229]\n      +- Project [userId#22, propertyId#44, rating#216, named_struct(propertyId, propertyId#44, rating, rating#216) AS Recommendations#229]\n         +- Project [userId#22, propertyId#44, rating#216]\n            +- Project [new_userId#207, new_propertyId#215, rating#216, userId#22, propertyId#44, weight#118]\n               +- Join Inner, ((new_userId#207 = new_userId#106) && (new_propertyId#215 = new_propertyId#112))\n                  :- Project [new_userId#207, recommendations#212.new_propertyId AS new_propertyId#215, recommendations#212.ra

In [18]:
printDf(final_df["Recommendations.rating"].orderBy('Recommendations.rating', ascending=False).show())

TypeError: 'Column' object is not callable

In [2]:
from pyspark.sql import functions as F
final_df1= (final_df.select("userId","propertyId","rating").withColumn("Recommendations", F.struct(F.col("propertyId"), F.col("rating")))).select("userId","Recommendations")



NameError: name 'final_df' is not defined

In [1]:
printDf(final_df1)

NameError: name 'printDf' is not defined

In [87]:
df2.registerTempTable("sql_table")

In [49]:
sqlContext.sql("""
    SELECT *, 100 * ratings/matrix_size AS percentage
    FROM (
        SELECT users, properties, ratings, users * properties AS matrix_size
        FROM (
            SELECT COUNT(*) AS ratings, COUNT(DISTINCT(propertyId)) AS properties, COUNT(DISTINCT(userId)) AS users
            FROM sql_table
        )c 
    )
""").show()

+-----+----------+-------+-----------+------------------+
|users|properties|ratings|matrix_size|        percentage|
+-----+----------+-------+-----------+------------------+
|  670|      2684|   5403|    1798280|0.3004537669328469|
+-----+----------+-------+-----------+------------------+



In [29]:
def printDf(sprkDF):
    newdf = sprkDF.toPandas()
    from IPython.display import display, HTML
    return HTML(newdf.to_html())

In [ ]:
'''
data_rem_cols=data["userId","properties.id","event"]
data=data1.drop('_corrupt_record','anonymousId','category','channel','_metadata','traits','writekey')

#data.groupBy("event").count().show(100)

In [160]:
df7 = df2.filter(df2.propertyId.isNotNull())

In [180]:
df2.filter(df2["new_propertyId"]!=0).show()

+--------------------+--------------------+------+----------+--------------+
|              userId|          propertyId|weight|new_userId|new_propertyId|
+--------------------+--------------------+------+----------+--------------+
|00081a0bd3f97331e...|5c975de87f80ae000...|    10|       186|           443|
|0025f9b8645ba1f13...|5c9102340c69a3000...|    10|        49|           230|
|0025f9b8645ba1f13...|5c911e7ceee13f000...|    10|        49|           239|
|0025f9b8645ba1f13...|5c911e8e48dd37000...|    10|        49|           434|
|0025f9b8645ba1f13...|5c911e83835437000...|    10|        49|             7|
|0032468214fb54875...|5c79221fd4c80c000...|    10|        50|            67|
|0032468214fb54875...|5c6c7b88d3216c000...|    10|        50|           466|
|0032468214fb54875...|5ca065cfd4c80c000...|    10|        50|           307|
|0032468214fb54875...|5c6f1e83f65bfd000...|    10|        50|           837|
|0062652d7ed45b3f3...|5c9b9c52b5d508000...|    10|       181|           361|

In [178]:
df100.where(col("propertyId").isNull()).show()

#df.where(col("dt_mvmt").isNotNull())

AttributeError: 'NoneType' object has no attribute 'where'

In [162]:
df7.filter(df7["propertyId"]=='          ').show()

+------+----------+------+----------+--------------+
|userId|propertyId|weight|new_userId|new_propertyId|
+------+----------+------+----------+--------------+
+------+----------+------+----------+--------------+



In [174]:
from pyspark.sql.functions import regexp_replace, col

df99=df2.select(regexp_replace(col("propertyId"), " ", ""))

In [176]:
from pyspark.sql.functions import trim

df100=df2.select(trim(col("propertyId"))).show()

+--------------------+
|    trim(propertyId)|
+--------------------+
|5c975de87f80ae000...|
|5c9102340c69a3000...|
|5c911e7ceee13f000...|
|5c911e8e48dd37000...|
|5c911e83835437000...|
|5c79221fd4c80c000...|
|5c6c7b88d3216c000...|
|5ca065cfd4c80c000...|
|5c6f1e83f65bfd000...|
|5c9b9c52b5d508000...|
|5c8a5908d4c80c000...|
|5c850d41d4c80c000...|
|5c8a5914d4c80c000...|
|5c2f95dcbc09e7000...|
|5c6974848e3276000...|
|5bbe6c227c1e90000...|
|5c87f6ecbe7c7e000...|
|5c77c15592596f000...|
|5c78aa83c5c1f1000...|
|5bea9c64733163000...|
+--------------------+
only showing top 20 rows



In [152]:
df7=df2.na.drop(subset=["propertyId"])

In [141]:
printDf(final_df)

In [101]:
from pyspark.sql import functions as F
final_df1= final_df.select("userId","propertyId","rating").withColumn("Recommendations", F.struct(F.col("propertyId"), F.col("rating")))




In [102]:
#final_df1.coalesce(1).write.format('json').save('output.json')

final_df1.select("userId", "Recommendations").write.save("output1.json",format="json")


In [114]:
final_df1.filter(final_df1['userId'] == '01ac2ec191319b9cf75901aadf385341').show()

+--------------------+--------------------+--------+--------------------+
|              userId|          propertyId|  rating|     Recommendations|
+--------------------+--------------------+--------+--------------------+
|01ac2ec191319b9cf...|5bf7639ebc09e7000...|9.952677|[5bf7639ebc09e700...|
|01ac2ec191319b9cf...|5bf7639ebc09e7000...|9.952677|[5bf7639ebc09e700...|
|01ac2ec191319b9cf...|5bf7639ebc09e7000...|9.952677|[5bf7639ebc09e700...|
|01ac2ec191319b9cf...|5b7edffb1f6d95000...|9.952677|[5b7edffb1f6d9500...|
|01ac2ec191319b9cf...|5b7edffb1f6d95000...|9.952677|[5b7edffb1f6d9500...|
|01ac2ec191319b9cf...|5b7edffb1f6d95000...|9.952677|[5b7edffb1f6d9500...|
|01ac2ec191319b9cf...|5bbf2203e0c5ed000...|9.952677|[5bbf2203e0c5ed00...|
|01ac2ec191319b9cf...|5c61eb2b8e3276000...|9.952677|[5c61eb2b8e327600...|
+--------------------+--------------------+--------+--------------------+



In [82]:
# Generate top 10 movie recommendations for each user
userRecs = model.recommendForAllUsers(10)

In [7]:
userRecs.printSchema()

root
 |-- new_userId: integer (nullable = false)
 |-- recommendations: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- new_propertyId: integer (nullable = true)
 |    |    |-- rating: float (nullable = true)



In [ ]:
userRecs5 = userRecs.select("new_userId","parking_types").withColumn("parking_types_array",F.explode("parking_types"))


In [ ]:
data.select(F.explode("properties").alias("properties")).select("properties.*")
    temp = propertydata.withColumn("images", F.explode("images"))
    temp=temp.groupBy("_id").count()
    joined_df1 = propertydata.join(temp,'_id','inner')
    joined_df2=getOneHotEncodingTransformation(transformed_propertydata=joined_df1)
    joined_df = joined_df1.join(joined_df2,'_id','inner')
    joined_df = joined_df.withColumn("price_cents", joined_df["price_cents"].cast(IntegerType()))
    joined_df = joined_df.withColumn("beds", joined_df["beds"].cast(IntegerType()))
    joined_df = joined_df.withColumn("bathrooms", joined_df["bathrooms"].cast(IntegerType()))
    return joined_df

In [ ]:
userRecs5 = userRecs.select("new_userId","parking_types").withColumn("parking_types_array",F.explode("parking_types"))


In [107]:
printDf(userRecs.filter(userRecs.new_userId==148))

#userRecs.filter(userRecs['new_userId'] == 176).collect()

In [83]:
from pyspark.sql import SQLContext,functions as F
aa=userRecs.withColumn("recommendations",F.explode("recommendations"))


In [84]:
aa.show()

+----------+----------------+
|new_userId| recommendations|
+----------+----------------+
|       148|[689, 19.251738]|
|       148|[345, 18.420998]|
|       148|[652, 16.537062]|
|       148|[771, 11.697708]|
|       148|[473, 11.697708]|
|       148|[675, 11.426103]|
|       148|[778, 11.426103]|
|       148|[283, 11.426103]|
|       148|[691, 11.426103]|
|       148|[336, 11.426103]|
|        31|[503, 19.486986]|
|        31|[632, 18.104445]|
|        31|[628, 15.010872]|
|        31|[257, 15.010872]|
|        31| [574, 12.48284]|
|        31| [38, 11.675124]|
|        31| [122, 9.952677]|
|        31| [151, 9.952677]|
|        31| [592, 9.952677]|
|        31| [440, 9.952677]|
+----------+----------------+
only showing top 20 rows



In [48]:
aa.printSchema()

root
 |-- new_userId: integer (nullable = false)
 |-- recommendations: struct (nullable = true)
 |    |-- new_propertyId: integer (nullable = true)
 |    |-- rating: float (nullable = true)



In [85]:
aa=aa.select("new_userId","recommendations.new_propertyId","recommendations.rating")


In [86]:
aa.show()

+----------+--------------+---------+
|new_userId|new_propertyId|   rating|
+----------+--------------+---------+
|       148|           689|19.251738|
|       148|           345|18.420998|
|       148|           652|16.537062|
|       148|           771|11.697708|
|       148|           473|11.697708|
|       148|           675|11.426103|
|       148|           778|11.426103|
|       148|           283|11.426103|
|       148|           691|11.426103|
|       148|           336|11.426103|
|        31|           503|19.486986|
|        31|           632|18.104445|
|        31|           628|15.010872|
|        31|           257|15.010872|
|        31|           574| 12.48284|
|        31|            38|11.675124|
|        31|           122| 9.952677|
|        31|           151| 9.952677|
|        31|           592| 9.952677|
|        31|           440| 9.952677|
+----------+--------------+---------+
only showing top 20 rows



In [79]:
aa_joined = aa.join(df2,['new_userId','new_propertyId'],'inner')

#df = df1.join(df2, (df1.x1 == df2.x1) & (df1.x2 == df2.x2))

In [80]:
aa_joined.show()

+----------+--------------+---------+--------------------+--------------------+------+
|new_userId|new_propertyId|   rating|              userId|          propertyId|weight|
+----------+--------------+---------+--------------------+--------------------+------+
|        31|           122| 9.952677|01ac2ec191319b9cf...|5bf7639ebc09e7000...|    10|
|        31|           122| 9.952677|01ac2ec191319b9cf...|5bf7639ebc09e7000...|    10|
|        31|           122| 9.952677|01ac2ec191319b9cf...|5bf7639ebc09e7000...|    10|
|        31|           151| 9.952677|01ac2ec191319b9cf...|5b7edffb1f6d95000...|    10|
|        31|           151| 9.952677|01ac2ec191319b9cf...|5b7edffb1f6d95000...|    10|
|        31|           151| 9.952677|01ac2ec191319b9cf...|5b7edffb1f6d95000...|    10|
|        31|           592| 9.952677|01ac2ec191319b9cf...|5bbf2203e0c5ed000...|    10|
|        31|           440| 9.952677|01ac2ec191319b9cf...|5c61eb2b8e3276000...|    10|
|        85|           767|29.975178|027f71

In [90]:
final_df.show()

+----------+--------------+---------+--------------------+--------------------+------+
|new_userId|new_propertyId|   rating|              userId|          propertyId|weight|
+----------+--------------+---------+--------------------+--------------------+------+
|        31|           122| 9.952677|01ac2ec191319b9cf...|5bf7639ebc09e7000...|    10|
|        31|           122| 9.952677|01ac2ec191319b9cf...|5bf7639ebc09e7000...|    10|
|        31|           122| 9.952677|01ac2ec191319b9cf...|5bf7639ebc09e7000...|    10|
|        31|           151| 9.952677|01ac2ec191319b9cf...|5b7edffb1f6d95000...|    10|
|        31|           151| 9.952677|01ac2ec191319b9cf...|5b7edffb1f6d95000...|    10|
|        31|           151| 9.952677|01ac2ec191319b9cf...|5b7edffb1f6d95000...|    10|
|        31|           592| 9.952677|01ac2ec191319b9cf...|5bbf2203e0c5ed000...|    10|
|        31|           440| 9.952677|01ac2ec191319b9cf...|5c61eb2b8e3276000...|    10|
|        85|           767|29.975178|027f71

In [101]:
userRecs.registerTempTable("userRecs_table")

In [136]:
sqlContext.sql("""
                select b.userId,
                (select b.propertyId from df2_table b where b.new_propertyId=recommendations.new_propertyId[0] and new_userId=b.new_userId) as property,
                recommendations.new_propertyId[2] as property,
                recommendations.new_propertyId[3] as property,
                recommendations.new_propertyId[4] as property,
                recommendations.new_propertyId[5] as property,
                recommendations.new_propertyId[6] as property,
                recommendations.new_propertyId[7] as property,
                recommendations.new_propertyId[8] as property,
                recommendations.new_propertyId[9] as property
                from userRecs_table as a, df2_table as b
                where a.new_userId=b.new_userId
               """).show()




AnalysisException: 'Correlated scalar subqueries must be aggregated: Filter ((new_propertyId#8536 = outer(recommendations#8639.new_propertyId AS new_propertyId#14239)[0]) && (new_userId#8530 = new_userId#8530))\n+- SubqueryAlias `b`\n   +- SubqueryAlias `df2_table`\n      +- Project [userId#8466, propertyId#8488, coalesce(weight#8542, cast(5 as int)) AS weight#8553, new_userId#8530, new_propertyId#8536]\n         +- Project [userId#8466, propertyId#8488, cast(weight#8498 as int) AS weight#8542, new_userId#8530, new_propertyId#8536]\n            +- Project [userId#8466, propertyId#8488, weight#8498, new_userId#8530, cast(new_propertyId#8524 as int) AS new_propertyId#8536]\n               +- Project [userId#8466, propertyId#8488, weight#8498, cast(new_userId#8519 as int) AS new_userId#8530, new_propertyId#8524]\n                  +- Project [userId#8466, propertyId#8488, weight#8498, new_userId#8519, UDF(cast(propertyId#8488 as string)) AS new_propertyId#8524]\n                     +- Pr

In [67]:
userRecs2=userRecs.collect()

In [72]:
userRecs2.registerTempTable("userRecs2_data")

AttributeError: 'list' object has no attribute 'registerTempTable'

In [68]:
printDf(userRecs.show())

+----------+--------------------+
|new_userId|     recommendations|
+----------+--------------------+
|      1580|[[633, 28.615274]...|
|      4900|[[633, 28.615274]...|
|      5300|[[633, 28.615274]...|
|      6620|[[633, 28.615274]...|
|      7240|[[633, 28.615274]...|
|      7340|[[633, 28.615274]...|
|      7880|[[633, 28.615274]...|
|      9900|[[633, 28.615274]...|
|     12940|[[633, 28.615274]...|
|     13840|[[633, 28.615274]...|
|     14450|[[633, 28.615274]...|
|     14570|[[633, 28.615274]...|
|     15790|[[633, 28.615274]...|
|       471|[[633, 28.615274]...|
|      1591|[[633, 28.615274]...|
|      4101|[[633, 28.615274]...|
|     11141|[[633, 28.615274]...|
|      1342|[[633, 28.615274]...|
|      2122|[[633, 28.615274]...|
|      2142|[[633, 28.615274]...|
+----------+--------------------+
only showing top 20 rows



AttributeError: 'NoneType' object has no attribute 'toPandas'

In [137]:
for i in userRecs2:
    for j in i.recommendations:
        print(i.new_userId, j.new_propertyId,j.rating)

1580 633 28.61527442932129
1580 424 28.15255355834961
1580 760 28.094545364379883
1580 768 28.093650817871094
1580 339 28.07642936706543
1580 659 28.000593185424805
1580 642 27.866762161254883
1580 608 27.657005310058594
1580 258 27.530288696289062
1580 629 27.530288696289062
4900 633 28.61527442932129
4900 424 28.15255355834961
4900 760 28.094545364379883
4900 768 28.093650817871094
4900 339 28.07642936706543
4900 659 28.000593185424805
4900 642 27.866762161254883
4900 608 27.657005310058594
4900 258 27.530288696289062
4900 629 27.530288696289062
5300 633 28.61527442932129
5300 424 28.15255355834961
5300 760 28.094545364379883
5300 768 28.093650817871094
5300 339 28.07642936706543
5300 659 28.000593185424805
5300 642 27.866762161254883
5300 608 27.657005310058594
5300 258 27.530288696289062
5300 629 27.530288696289062
6620 633 28.61527442932129
6620 424 28.15255355834961
6620 760 28.094545364379883
6620 768 28.093650817871094
6620 339 28.07642936706543
6620 659 28.000593185424805
6620

10081 642 27.866762161254883
10081 608 27.657005310058594
10081 258 27.530288696289062
10081 629 27.530288696289062
10121 633 28.61527442932129
10121 424 28.15255355834961
10121 760 28.094545364379883
10121 768 28.093650817871094
10121 339 28.07642936706543
10121 659 28.000593185424805
10121 642 27.866762161254883
10121 608 27.657005310058594
10121 258 27.530288696289062
10121 629 27.530288696289062
12471 633 28.61527442932129
12471 424 28.15255355834961
12471 760 28.094545364379883
12471 768 28.093650817871094
12471 339 28.07642936706543
12471 659 28.000593185424805
12471 642 27.866762161254883
12471 608 27.657005310058594
12471 258 27.530288696289062
12471 629 27.530288696289062
12611 633 28.61527442932129
12611 424 28.15255355834961
12611 760 28.094545364379883
12611 768 28.093650817871094
12611 339 28.07642936706543
12611 659 28.000593185424805
12611 642 27.866762161254883
12611 608 27.657005310058594
12611 258 27.530288696289062
12611 629 27.530288696289062
13261 633 28.6152744293

5173 608 27.657005310058594
5173 258 27.530288696289062
5173 629 27.530288696289062
9383 633 28.61527442932129
9383 424 28.15255355834961
9383 760 28.094545364379883
9383 768 28.093650817871094
9383 339 28.07642936706543
9383 659 28.000593185424805
9383 642 27.866762161254883
9383 608 27.657005310058594
9383 258 27.530288696289062
9383 629 27.530288696289062
11393 633 28.61527442932129
11393 424 28.15255355834961
11393 760 28.094545364379883
11393 768 28.093650817871094
11393 339 28.07642936706543
11393 659 28.000593185424805
11393 642 27.866762161254883
11393 608 27.657005310058594
11393 258 27.530288696289062
11393 629 27.530288696289062
12393 633 28.61527442932129
12393 424 28.15255355834961
12393 760 28.094545364379883
12393 768 28.093650817871094
12393 339 28.07642936706543
12393 659 28.000593185424805
12393 642 27.866762161254883
12393 608 27.657005310058594
12393 258 27.530288696289062
12393 629 27.530288696289062
13483 633 28.61527442932129
13483 424 28.15255355834961
13483 760

3098 768 28.093650817871094
3098 339 28.07642936706543
3098 659 28.000593185424805
3098 642 27.866762161254883
3098 608 27.657005310058594
3098 258 27.530288696289062
3098 629 27.530288696289062
4078 633 28.61527442932129
4078 424 28.15255355834961
4078 760 28.094545364379883
4078 768 28.093650817871094
4078 339 28.07642936706543
4078 659 28.000593185424805
4078 642 27.866762161254883
4078 608 27.657005310058594
4078 258 27.530288696289062
4078 629 27.530288696289062
5308 633 28.61527442932129
5308 424 28.15255355834961
5308 760 28.094545364379883
5308 768 28.093650817871094
5308 339 28.07642936706543
5308 659 28.000593185424805
5308 642 27.866762161254883
5308 608 27.657005310058594
5308 258 27.530288696289062
5308 629 27.530288696289062
6598 633 28.61527442932129
6598 424 28.15255355834961
6598 760 28.094545364379883
6598 768 28.093650817871094
6598 339 28.07642936706543
6598 659 28.000593185424805
6598 642 27.866762161254883
6598 608 27.657005310058594
6598 258 27.530288696289062
65

13398 258 27.530288696289062
13398 629 27.530288696289062
879 633 28.61527442932129
879 424 28.15255355834961
879 760 28.094545364379883
879 768 28.093650817871094
879 339 28.07642936706543
879 659 28.000593185424805
879 642 27.866762161254883
879 608 27.657005310058594
879 258 27.530288696289062
879 629 27.530288696289062
2249 633 28.61527442932129
2249 424 28.15255355834961
2249 760 28.094545364379883
2249 768 28.093650817871094
2249 339 28.07642936706543
2249 659 28.000593185424805
2249 642 27.866762161254883
2249 608 27.657005310058594
2249 258 27.530288696289062
2249 629 27.530288696289062
12249 633 28.61527442932129
12249 424 28.15255355834961
12249 760 28.094545364379883
12249 768 28.093650817871094
12249 339 28.07642936706543
12249 659 28.000593185424805
12249 642 27.866762161254883
12249 608 27.657005310058594
12249 258 27.530288696289062
12249 629 27.530288696289062
13329 633 28.61527442932129
13329 424 28.15255355834961
13329 760 28.094545364379883
13329 768 28.0936508178710

...

10711 659 28.000593185424805
10711 642 27.866762161254883
10711 608 27.657005310058594
10711 258 27.530288696289062
10711 629 27.530288696289062
12021 633 28.61527442932129
12021 424 28.15255355834961
12021 760 28.094545364379883
12021 768 28.093650817871094
12021 339 28.07642936706543
12021 659 28.000593185424805
12021 642 27.866762161254883
12021 608 27.657005310058594
12021 258 27.530288696289062
12021 629 27.530288696289062
12451 633 28.61527442932129
12451 424 28.15255355834961
12451 760 28.094545364379883
12451 768 28.093650817871094
12451 339 28.07642936706543
12451 659 28.000593185424805
12451 642 27.866762161254883
12451 608 27.657005310058594
12451 258 27.530288696289062
12451 629 27.530288696289062
15941 448 16.023340225219727
15941 575 14.83536148071289
15941 346 14.3140869140625
15941 772 12.710412979125977
15941 474 12.710412979125977
15941 729 9.970279693603516
15941 749 9.970279693603516
15941 417 7.379715442657471
15941 677 6.281662464141846
15941 284 6.043293952941894

2095 608 27.657005310058594
2095 258 27.530288696289062
2095 629 27.530288696289062
4985 633 28.61527442932129
4985 424 28.15255355834961
4985 760 28.094545364379883
4985 768 28.093650817871094
4985 339 28.07642936706543
4985 659 28.000593185424805
4985 642 27.866762161254883
4985 608 27.657005310058594
4985 258 27.530288696289062
4985 629 27.530288696289062
8065 633 28.61527442932129
8065 424 28.15255355834961
8065 760 28.094545364379883
8065 768 28.093650817871094
8065 339 28.07642936706543
8065 659 28.000593185424805
8065 642 27.866762161254883
8065 608 27.657005310058594
8065 258 27.530288696289062
8065 629 27.530288696289062
11095 633 28.61527442932129
11095 424 28.15255355834961
11095 760 28.094545364379883
11095 768 28.093650817871094
11095 339 28.07642936706543
11095 659 28.000593185424805
11095 642 27.866762161254883
11095 608 27.657005310058594
11095 258 27.530288696289062
11095 629 27.530288696289062
4196 633 28.61527442932129
4196 424 28.15255355834961
4196 760 28.094545364

841 768 28.093650817871094
841 339 28.07642936706543
841 659 28.000593185424805
841 642 27.866762161254883
841 608 27.657005310058594
841 258 27.530288696289062
841 629 27.530288696289062
991 633 28.61527442932129
991 424 28.15255355834961
991 760 28.094545364379883
991 768 28.093650817871094
991 339 28.07642936706543
991 659 28.000593185424805
991 642 27.866762161254883
991 608 27.657005310058594
991 258 27.530288696289062
991 629 27.530288696289062
3291 633 28.61527442932129
3291 424 28.15255355834961
3291 760 28.094545364379883
3291 768 28.093650817871094
3291 339 28.07642936706543
3291 659 28.000593185424805
3291 642 27.866762161254883
3291 608 27.657005310058594
3291 258 27.530288696289062
3291 629 27.530288696289062
5301 633 28.61527442932129
5301 424 28.15255355834961
5301 760 28.094545364379883
5301 768 28.093650817871094
5301 339 28.07642936706543
5301 659 28.000593185424805
5301 642 27.866762161254883
5301 608 27.657005310058594
5301 258 27.530288696289062
5301 629 27.5302886

14307 339 28.07642936706543
14307 659 28.000593185424805
14307 642 27.866762161254883
14307 608 27.657005310058594
14307 258 27.530288696289062
14307 629 27.530288696289062
16097 633 28.61527442932129
16097 424 28.15255355834961
16097 760 28.094545364379883
16097 768 28.093650817871094
16097 339 28.07642936706543
16097 659 28.000593185424805
16097 642 27.866762161254883
16097 608 27.657005310058594
16097 258 27.530288696289062
16097 629 27.530288696289062
788 633 28.61527442932129
788 424 28.15255355834961
788 760 28.094545364379883
788 768 28.093650817871094
788 339 28.07642936706543
788 659 28.000593185424805
788 642 27.866762161254883
788 608 27.657005310058594
788 258 27.530288696289062
788 629 27.530288696289062
4178 633 28.61527442932129
4178 424 28.15255355834961
4178 760 28.094545364379883
4178 768 28.093650817871094
4178 339 28.07642936706543
4178 659 28.000593185424805
4178 642 27.866762161254883
4178 608 27.657005310058594
4178 258 27.530288696289062
4178 629 27.530288696289

10064 608 27.657005310058594
10064 258 27.530288696289062
10064 629 27.530288696289062
15274 633 28.61527442932129
15274 424 28.15255355834961
15274 760 28.094545364379883
15274 768 28.093650817871094
15274 339 28.07642936706543
15274 659 28.000593185424805
15274 642 27.866762161254883
15274 608 27.657005310058594
15274 258 27.530288696289062
15274 629 27.530288696289062
15574 633 28.61527442932129
15574 424 28.15255355834961
15574 760 28.094545364379883
15574 768 28.093650817871094
15574 339 28.07642936706543
15574 659 28.000593185424805
15574 642 27.866762161254883
15574 608 27.657005310058594
15574 258 27.530288696289062
15574 629 27.530288696289062
315 633 28.61527442932129
315 424 28.15255355834961
315 760 28.094545364379883
315 768 28.093650817871094
315 339 28.07642936706543
315 659 28.000593185424805
315 642 27.866762161254883
315 608 27.657005310058594
315 258 27.530288696289062
315 629 27.530288696289062
5745 633 28.61527442932129
5745 424 28.15255355834961
5745 760 28.094545

In [ ]:
# Generate top 10 movie recommendations for each user
userRecs = model.recommendForAllUsers(10)
# Generate top 10 user recommendations for each movie
movieRecs = model.recommendForAllItems(10)

# Generate top 10 movie recommendations for a specified set of users
users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)
# Generate top 10 user recommendations for a specified set of movies
movies = ratings.select(als.getItemCol()).distinct().limit(3)
movieSubSetRecs = model.recommendForItemSubset(movies, 10)

users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)

In [ ]:
users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)


In [121]:
als.getUserCol()

'new_userId'

In [24]:
user85Recs = userRecs.filter(userRecs['new_userId'] == 176).collect()

In [25]:
for row in user85Recs:
    for rec in row.recommendations:
        print(rec.new_propertyId,rec.rating)
            

695 68.62165832519531
228 68.1855239868164
3 58.20518112182617
798 57.75914001464844
37 50.14998245239258
481 48.738460540771484
262 48.35060501098633
675 48.35060501098633
501 47.85987091064453
491 47.85987091064453


In [ ]:
'''
#Pandas integration
#PySpark DataFrames and Pandas DataFrames interact very easily with each other. For example, if I have an existing Pandas DataFrame, to convert it to PySpark we simply do:

df = sc.DataFrame(pandas_df)
#And to convert a PySpark DataFrame to Pandas, use the toPandas() function:

pandas_df = df.toPandas()
#Remember, converting a Spark DataFrame to a Pandas DataFrame means that you're asking Python to put all of the data into the RAM of a single machine. Be careful or the system may crash because it ran out of memory.


In [62]:
!python --version


Python 3.7.1


In [4]:
sc

In [15]:
sc1 = sc.sparkContext

In [45]:
EVENTS_MAPPING=sc1.textFile("events.txt")

In [51]:
pandas_df = EVENTS_MAPPING.toPandas()

AttributeError: 'RDD' object has no attribute 'toPandas'

In [46]:
EVENTS_MAPPING.collect()

['{"Favorited":"10","PartnerCTAClicked":"20"}']

In [59]:
f = open("events.txt","a") 

In [60]:
lines = f.readlines()

UnsupportedOperation: not readable

In [49]:
df2 = df.replace(to_replace=dict(EVENTS_MAPPING), subset=['weight'])

TypeError: RDD.keys() returned a non-iterable (type PipelinedRDD)

In [62]:
df.registerTempTable("table")

In [68]:
df=sqlContext.sql("select userId," 
    	+ " substr(context.page.path,11,length(context.page.path)) as propertyId,"
    

+--------------------+--------------------+------------+
|              userId|          propertyId|      weight|
+--------------------+--------------------+------------+
|00081a0bd3f97331e...|5c975de87f80ae000...|PhotoClicked|
|00081a0bd3f97331e...|5c975de87f80ae000...|PhotoClicked|
|0025f9b8645ba1f13...|5c9102340c69a3000...|PhotoClicked|
|0025f9b8645ba1f13...|5c911e8e48dd37000...|PhotoClicked|
|0025f9b8645ba1f13...|5c911e83835437000...|PhotoClicked|
|0025f9b8645ba1f13...|5c9102340c69a3000...|PhotoClicked|
|0025f9b8645ba1f13...|5c9102340c69a3000...|PhotoClicked|
|0025f9b8645ba1f13...|5c911e7ceee13f000...|PhotoClicked|
|0032468214fb54875...|5ca065cfd4c80c000...|PhotoClicked|
|0032468214fb54875...|5c6f1e83f65bfd000...|PhotoClicked|
|0032468214fb54875...|5c79221fd4c80c000...|PhotoClicked|
|0032468214fb54875...|5c6c7b88d3216c000...|PhotoClicked|
|0062652d7ed45b3f3...|5c9b9c52b5d508000...|PhotoClicked|
|0075dd2db13a24f9b...|5c8a5914d4c80c000...|PhotoClicked|
|0075dd2db13a24f9b...|5c850d41d

In [64]:
################
sqlContext.sql("select count(*) from table").show()

+--------+
|count(1)|
+--------+
|  143511|
+--------+



In [ ]:
################
#GROUPBY
################

df1.groupby("event").count().orderBy('count', ascending=False).show()


In [6]:
from nest_recom_constants import (
	FILE_PATH, 
	NUM_RECOM_PER_USR
	)

In [7]:
print(FILE_PATH)

/Users/jatinmalhotra/Desktop/not/


In [2]:

import pyspark
from pyspark.sql import SparkSession
from pyspark import SparkConf,SparkContext
from pyspark.sql import SQLContext,functions as F

from nest_recom_spark_session import nest_get_spark_session

# Load Json to spark dataframe
from nest_recom_loader import load_spark_df

from nest_recom_event_mapper import (
	map_weights, 
	numeric_conversion
)

from nest_recom_constants import (
	FILE_PATH, 
	NUM_RECOM_PER_USR
	)

from nest_recom_als_model import nest_recom_als


def set_spark_local():
	l_obj=nest_get_spark_session()

	sc,sqlContext = l_obj.start_or_get_spark(
					app_name="NestReadyRecommendationEngine", 
					url='local[2]',
					memory="20g"
					)
	return sc, sqlContext


# comment it when running in production
sc,sqlContext = set_spark_local()



data=load_spark_df(sqlContext,FILE_PATH,'FULL')

#print(data.count())




df = map_weights(data,sc,sqlContext)


# popularity matrix
popularity_df = nest_recom_als.popularity_matrix(df)
popularity_df.show()



df1 = numeric_conversion(df)


nest_recom_als=nest_recom_als()



# COllaborative Filtering (User Behaviour )
model=nest_recom_als.als_algo(df1)


'''
model.write().overwrite().save("nest_recom_trained_model")
from pyspark.ml.recommendation import ALSModel
h=ALSModel.load("nest_recom_trained_model")
userRecs = h.recommendForAllUsers(5)
user85Recs = userRecs.filter(userRecs['new_userId'] == 1).collect()

for row in user85Recs:
    for rec in row.recommendations:
        print(rec.new_propertyId,rec.rating)

'''

#als_df=nest_recom_als.recommend(NUM_RECOM_PER_USR,model,df1)


#als_df.show()




+--------------------+----------+
|          propertyId|avg_weight|
+--------------------+----------+
|                    |      18.0|
|5c752d7fd4c80c000...|       3.0|
|5c4c5592dc2e4d000...|       3.0|
|5c67fea4d4c80c000...|       2.0|
|5c8bae3db5d508000...|       2.0|
|5c6923208e3276000...|       2.0|
|5c911e83835437000...|       2.0|
|5c4763c98e3276000...|       2.0|
|5c7e5cf8a080c4000...|       2.0|
|5c5ca33f8e3276000...|       2.0|
|5bc72835ee13c6000...|       2.0|
|5c8c9482be7c7e000...|       2.0|
|5c7f5de164ad71000...|       2.0|
|5bbe6d847c1e90000...|       2.0|
|5c4c5444dc2e4d000...|       2.0|
|5c78fd9cc5c1f1000...|       2.0|
|5c827448be7c7e000...|       2.0|
|5c7507b4c5c1f1000...|       2.0|
|5c6e9670d4c80c000...|       2.0|
|5c6fe7c2d4c80c000...|       2.0|
+--------------------+----------+
only showing top 20 rows



AttributeError: 'nest_recom_als' object has no attribute '_jdf'

In [11]:
from nest_recom_als_model import nest_recom_als1
nest_recom_als=nest_recom_als()



# COllaborative Filtering (User Behaviour )
model=nest_recom_als.als_algo(df1,'FULL')


ImportError: cannot import name 'nest_recom_als1' from 'nest_recom_als_model' (/Users/jatinmalhotra/Desktop/NestReady_Recommendation_System/CODING/nest_recommendation_engine/nest_recom_als_model.py)

In [2]:
data.show()

+--------------------+--------------------+--------+-------+--------------------+-----+--------------------+--------+--------------------+----------+--------------------+--------------------+--------------------+--------------------+------+-----+--------------------+-------+--------------------+
|           _metadata|         anonymousId|category|channel|             context|event|           messageId|    name|   originalTimestamp| projectId|          properties|          receivedAt|              sentAt|           timestamp|traits| type|              userId|version|            writeKey|
+--------------------+--------------------+--------+-------+--------------------+-----+--------------------+--------+--------------------+----------+--------------------+--------------------+--------------------+--------------------+------+-----+--------------------+-------+--------------------+
|[[Google Analytic...|e429ee69-46ad-4fd...|    null| client|[[55497169, email...| null|ajs-afa0c423b905d...| 

In [2]:
df = map_weights(data,sc,sqlContext)

In [16]:
from nest_recom_constants import (
	FILE_PATH, 
	NUM_RECOM_PER_USR,
	MODE
	)

In [14]:
model=nest_recom_als.als_algo()

NameError: name 'mode' is not defined

In [9]:
df1 = numeric_conversion(df)

In [10]:
df1.show()

+--------------------+--------------------+------+--------------+----------+
|              userId|          propertyId|weight|new_propertyId|new_userId|
+--------------------+--------------------+------+--------------+----------+
|00081a0bd3f97331e...|5c975de87f80ae000...|     1|           443|       186|
|0025f9b8645ba1f13...|5c9102340c69a3000...|     1|           230|        49|
|0025f9b8645ba1f13...|5c911e7ceee13f000...|     1|           239|        49|
|0025f9b8645ba1f13...|5c911e8e48dd37000...|     1|           434|        49|
|0025f9b8645ba1f13...|5c911e83835437000...|     1|             7|        49|
|0032468214fb54875...|5c79221fd4c80c000...|     1|            67|        50|
|0032468214fb54875...|5c6c7b88d3216c000...|     1|           466|        50|
|0032468214fb54875...|5ca065cfd4c80c000...|     1|           307|        50|
|0032468214fb54875...|5c6f1e83f65bfd000...|     1|           837|        50|
|0062652d7ed45b3f3...|5c9b9c52b5d508000...|     1|           361|       181|

In [6]:
popularity_df = popularity_matrix1(df)

In [8]:
popularity_df.count()

888

In [34]:
 data = df.cache() \
            .groupBy("propertyId") \
            .agg(F.sum(df.weight)) \
            .withColumnRenamed('sum(weight)', 'avg_weight') \
            .orderBy('avg_weight', ascending=False)
    
    
            #.agg({'weight':'avg'}) \
            #.withColumnRenamed('avg(weight)', 'avg_weight') \
          

In [18]:
    from pyspark.ml.recommendation import ALS
    import time
    from pyspark.sql import SQLContext,functions as F
    from pyspark.ml.recommendation import ALSModel

    def als_algo(data,MODE):
        
        als = ALS(userCol="new_userId", 
                  itemCol="new_propertyId", 
                  ratingCol="weight",
                  coldStartStrategy="nan"
                  )
        
        #start_time = time.time()
        #train_time = time.time() - start_time
        #print("Took {} seconds for training.".format(train_time))
    
        '''
        Save and Load Models
        model.write().overwrite().save("nest_recom_trained_model2")
        from pyspark.ml.recommendation import ALSModel
        h=ALSModel.load("nest_recom_trained_model")

        '''

        if (MODE=='DAILY'):

            # Load the trained model
            trained_model=ALSModel.load("nest_recom_trained_model")
            model=trained_model.fit(data)
           
        else:
            model = als.fit(data)
          
        # Save trained Model
        model.write().overwrite().save("nest_recom_trained_model")
       
        return model

In [21]:
a=als_algo(df1,'FULL')

In [37]:
a.explainParams

<bound method Params.explainParams of ALS_5a94eedec713>

In [35]:
b

<bound method Transformer.transform of ALS_5a94eedec713>

In [26]:
als_df=recommend1(10,a,df1)

In [30]:
printDf(als_df)

In [31]:
from pyspark.ml.recommendation import ALSModel
trained_model=ALSModel.load("nest_recom_trained_model")


AttributeError: 'ALSModel' object has no attribute 'fit'

In [32]:
trained_model.show()

AttributeError: 'ALSModel' object has no attribute 'show'

In [24]:
def recommend1(num,model,df2):

        userRecs = model.recommendForAllUsers(num)
        

        aa = userRecs.withColumn("recommendations",F.explode("recommendations"))

        aa = aa.select("new_userId","recommendations.new_propertyId","recommendations.rating")
        
        #aa_joined = aa.join(df2,['new_userId','new_propertyId'],'inner')
        aa_joined = aa.join(df2,['new_userId','new_propertyId'])

        #df = df1.join(df2, (df1.x1 == df2.x1) & (df1.x2 == df2.x2))
        
        final_df1= (aa_joined.select("userId","propertyId","rating").withColumn("Recommendations", F.struct(F.col("propertyId"), F.col("rating")))).select("userId","Recommendations")



        return final_df1

In [42]:
from datetime import datetime
l_date = datetime.today().strftime('%Y%m')
l_file_name='/Users/jatinmalhotra/Desktop/not2/' + l_date + '/'

In [46]:
l_table_name='DAILY'+l_date

In [47]:
print(l_table_name)
        

DAILY201904


In [54]:
sqlContext.sql("SELECT count(1) FROM {} where 1=2".format(l_table_name+'1'))

DataFrame[count(1): bigint]

In [62]:

df.write.mode("append").saveAsTable(l_table_name+'2')

In [44]:
sqlContext.sql("SELECT count(1) FROM {} where 1=2".format(l_table_name))

NameError: name 'l_table_name' is not defined

In [65]:

import pyspark
from pyspark.sql import SparkSession
from pyspark import SparkConf,SparkContext
from pyspark.sql import SQLContext,functions as F

from nest_recom_spark_session import nest_get_spark_session

# Load Json to spark dataframe
from nest_recom_loader import load_spark_df

from nest_recom_event_mapper import (
	map_weights, 
	numeric_conversion
)

from nest_recom_constants import (
	FILE_PATH, 
	NUM_RECOM_PER_USR,
	MODE
	)

from nest_recom_als_model import nest_recom_als


def set_spark_local():
	l_obj=nest_get_spark_session()

	sc,sqlContext = l_obj.start_or_get_spark(
					app_name="NestReadyRecommendationEngine", 
					url='local[2]',
					memory="20g"
					)
	return sc, sqlContext

def set_spark_prod():
	
	sc = SparkContext(appName="NestReadyRecommendationEngine")
	sqlContext=SQLContext(sc)
	
	return sc, sqlContext


# comment it when running in production
sc,sqlContext = set_spark_local()


#sc,sqlContext = set_spark_prod()


data=load_spark_df(sqlContext,FILE_PATH,MODE)

#print(data.count())



df = map_weights(data,sc,sqlContext)


nest_recom_als=nest_recom_als()

# popularity matrix
popularity_df = nest_recom_als.popularity_matrix(df)
popularity_df.show()



df1 = numeric_conversion(df)





# COllaborative Filtering (User Behaviour )
#model=nest_recom_als.als_algo(df1,MODE)


'''
model.write().overwrite().save("nest_recom_trained_model")
from pyspark.ml.recommendation import ALSModel
h=ALSModel.load("nest_recom_trained_model")
userRecs = h.recommendForAllUsers(5)
user85Recs = userRecs.filter(userRecs['new_userId'] == 1).collect()

for row in user85Recs:
    for rec in row.recommendations:
        print(rec.new_propertyId,rec.rating)

'''

#als_df=nest_recom_als.recommend(NUM_RECOM_PER_USR,model,df1)


#als_df.show()




+--------------------+----------+
|          propertyId|avg_weight|
+--------------------+----------+
|                    |      18.0|
|5c752d7fd4c80c000...|       3.0|
|5c4c5592dc2e4d000...|       3.0|
|5c67fea4d4c80c000...|       2.0|
|5c8bae3db5d508000...|       2.0|
|5c6923208e3276000...|       2.0|
|5c911e83835437000...|       2.0|
|5c4763c98e3276000...|       2.0|
|5c7e5cf8a080c4000...|       2.0|
|5c5ca33f8e3276000...|       2.0|
|5bc72835ee13c6000...|       2.0|
|5c8c9482be7c7e000...|       2.0|
|5c7f5de164ad71000...|       2.0|
|5bbe6d847c1e90000...|       2.0|
|5c4c5444dc2e4d000...|       2.0|
|5c78fd9cc5c1f1000...|       2.0|
|5c827448be7c7e000...|       2.0|
|5c7507b4c5c1f1000...|       2.0|
|5c6e9670d4c80c000...|       2.0|
|5c6fe7c2d4c80c000...|       2.0|
+--------------------+----------+
only showing top 20 rows



'\nmodel.write().overwrite().save("nest_recom_trained_model")\nfrom pyspark.ml.recommendation import ALSModel\nh=ALSModel.load("nest_recom_trained_model")\nuserRecs = h.recommendForAllUsers(5)\nuser85Recs = userRecs.filter(userRecs[\'new_userId\'] == 1).collect()\n\nfor row in user85Recs:\n    for rec in row.recommendations:\n        print(rec.new_propertyId,rec.rating)\n\n'

In [66]:
df1.show()

+--------------------+--------------------+------+----------+--------------+
|              userId|          propertyId|weight|new_userId|new_propertyId|
+--------------------+--------------------+------+----------+--------------+
|00081a0bd3f97331e...|5c975de87f80ae000...|     1|       186|           443|
|0025f9b8645ba1f13...|5c9102340c69a3000...|     1|        49|           230|
|0025f9b8645ba1f13...|5c911e7ceee13f000...|     1|        49|           239|
|0025f9b8645ba1f13...|5c911e8e48dd37000...|     1|        49|           434|
|0025f9b8645ba1f13...|5c911e83835437000...|     1|        49|             7|
|0032468214fb54875...|5c79221fd4c80c000...|     1|        50|            67|
|0032468214fb54875...|5c6c7b88d3216c000...|     1|        50|           466|
|0032468214fb54875...|5ca065cfd4c80c000...|     1|        50|           307|
|0032468214fb54875...|5c6f1e83f65bfd000...|     1|        50|           837|
|0062652d7ed45b3f3...|5c9b9c52b5d508000...|     1|       181|           361|

In [68]:
from pyspark.ml.recommendation import ALS
import time
from pyspark.sql import SQLContext,functions as F
from pyspark.ml.recommendation import ALSModel
als = ALS(userCol="new_userId", 
                  itemCol="new_propertyId", 
                  ratingCol="weight",
                  coldStartStrategy="nan"
                  )
model = als.fit(df1)

In [75]:
userRecs = model.recommendForAllUsers(5)

In [ ]:
user85Recs = userRecs.filter(userRecs['new_userId'] == 176).collect()

for row in user85Recs:
    for rec in row.recommendations:
        print(rec.new_propertyId,rec.rating)
            

In [76]:
userRecs.show()

+----------+--------------------+
|new_userId|     recommendations|
+----------+--------------------+
|       148|[[418, 0.8998625]...|
|        31|[[275, 0.8998626]...|
|        85|[[410, 0.8998625]...|
|       137|[[363, 0.89986247...|
|        65|[[595, 0.8998625]...|
|        53|[[816, 0.8998625]...|
|        78|[[876, 0.8998625]...|
|       155|[[92, 0.8998625],...|
|       108|[[333, 0.89986265...|
|       193|[[30, 0.89986247]...|
|        34|[[763, 0.8998625]...|
|       101|[[5, 0.902447], [...|
|       115|[[853, 0.8998625]...|
|       126|[[220, 0.89986265...|
|        81|[[433, 0.8998625]...|
|       183|[[749, 0.8998626]...|
|        28|[[813, 0.8998625]...|
|        76|[[316, 0.8998626]...|
|        26|[[708, 0.8998625]...|
|        27|[[495, 0.89986247...|
+----------+--------------------+
only showing top 20 rows



In [77]:
aa = userRecs.withColumn("recommendations",F.explode("recommendations"))

In [78]:
aa.show()

+----------+-----------------+
|new_userId|  recommendations|
+----------+-----------------+
|       148| [418, 0.8998625]|
|       148|[117, 0.71704954]|
|       148| [804, 0.6414136]|
|       148| [404, 0.6335583]|
|       148| [791, 0.5610646]|
|        31| [275, 0.8998626]|
|        31| [304, 0.8998626]|
|        31| [742, 0.8998626]|
|        31| [532, 0.8998626]|
|        31| [726, 0.8998626]|
|        85| [410, 0.8998625]|
|        85| [693, 0.8998625]|
|        85| [101, 0.7045752]|
|        85| [250, 0.7045752]|
|        85| [593, 0.7045752]|
|       137|[363, 0.89986247]|
|       137|[697, 0.65710306]|
|       137|[843, 0.65710306]|
|       137| [74, 0.65710306]|
|       137|[329, 0.65710306]|
+----------+-----------------+
only showing top 20 rows



In [4]:
als_df.printSchema()

root
 |-- userId: string (nullable = true)
 |-- Recommendations: struct (nullable = false)
 |    |-- propertyId: string (nullable = true)
 |    |-- rating: float (nullable = true)



In [35]:
person = {
        'first_name': "John",
        "isAlive": True,
        "age": 27
        }

lis = ['a','b','c']

In [36]:


#final_df1.coalesce(1).write.format('json').save('output.json')

#als_df.select("userId", "Recommendations").write.save("output1.json",format="json")
import json
with open("person.json",'w') as fp:
    #json.dumps(person,fp)
    fp.write(lis)


TypeError: write() argument must be str, not list

In [61]:
#als_pd=als_df.select("userId", "Recommendations").toJSON()


#als_j=als_df.toJSON()

#json_string = json.dumps(als_df)


als_df.coalesce(1).write.format('json').save('aa.json')


In [79]:
als_df.show()

+--------------------+--------------------+
|              userId|     Recommendations|
+--------------------+--------------------+
|0e691f3840a8b4bd3...|[5c695e21d4c80c00...|
|27452dd2e1a70ca2f...|[5c787e4cc5c1f100...|
|27452dd2e1a70ca2f...|[5c823390be7c7e00...|
|27452dd2e1a70ca2f...|[5bbe6f1c7c1e9000...|
|27452dd2e1a70ca2f...|[5c7a9c3dc5c1f100...|
|27452dd2e1a70ca2f...|[5c50d7388e327600...|
|27452dd2e1a70ca2f...|[5bedb3ca73316300...|
|27452dd2e1a70ca2f...|[5c570b908e327600...|
|027f71d9d6351ec3a...|[chedule/5c96251f...|
|027f71d9d6351ec3a...|[5ca13ffb5a8dd600...|
|119e3cd34ea146edf...|[5c5bf1dd8e327600...|
|0bc2e7b1349c3d915...|[5c4bc8c98e327600...|
|0bc2e7b1349c3d915...|[5c694d0a8e327600...|
|0bc2e7b1349c3d915...|[5c6952828e327600...|
|3302b5091c9287e82...|[5c693a508e327600...|
|3302b5091c9287e82...|[5c62a87f8e327600...|
|3302b5091c9287e82...|[5c5c32df8e327600...|
|3302b5091c9287e82...|[5c6297298e327600...|
|19db47fec8cc8327f...|[5c54514bf5124b00...|
|19db47fec8cc8327f...|[5c19085b9

In [98]:
from pyspark.sql.functions import lit
als_df1=als_df.withColumn("new_column", lit(10))

In [106]:
als_df1.show()

+--------------------+--------------------+----------+
|              userId|     Recommendations|new_column|
+--------------------+--------------------+----------+
|0e691f3840a8b4bd3...|[5c695e21d4c80c00...|        10|
|27452dd2e1a70ca2f...|[5c787e4cc5c1f100...|        10|
|27452dd2e1a70ca2f...|[5c823390be7c7e00...|        10|
|27452dd2e1a70ca2f...|[5bbe6f1c7c1e9000...|        10|
|27452dd2e1a70ca2f...|[5c7a9c3dc5c1f100...|        10|
|27452dd2e1a70ca2f...|[5c50d7388e327600...|        10|
|27452dd2e1a70ca2f...|[5bedb3ca73316300...|        10|
|27452dd2e1a70ca2f...|[5c570b908e327600...|        10|
|027f71d9d6351ec3a...|[chedule/5c96251f...|        10|
|027f71d9d6351ec3a...|[5ca13ffb5a8dd600...|        10|
|119e3cd34ea146edf...|[5c5bf1dd8e327600...|        10|
|0bc2e7b1349c3d915...|[5c4bc8c98e327600...|        10|
|0bc2e7b1349c3d915...|[5c694d0a8e327600...|        10|
|0bc2e7b1349c3d915...|[5c6952828e327600...|        10|
|3302b5091c9287e82...|[5c693a508e327600...|        10|
|3302b5091

In [126]:

import numpy as np

als_new1=als_df1.groupby("new_column").agg(F.collect_list(np.array("UserId","Recommendations")).alias("UserId","Recommendations"))



TypeError: data type "Recommendations" not understood

AttributeError: 'DataFrame' object has no attribute 'Recommendations'

In [113]:
als_new1.show()

+----------+--------------------+
|new_column|     Recommendations|
+----------+--------------------+
|        10|[[5c695e21d4c80c0...|
+----------+--------------------+



In [114]:
als_new1.coalesce(1).write.format('json').save('dd.json')

In [60]:
print(als_j)

MapPartitionsRDD[549] at toJavaRDD at NativeMethodAccessorImpl.java:0


In [47]:
print(json_string)

{"first_name": "John", "isAlive": true, "age": 27}


In [44]:
als_pd.to_json("aa.json")

AttributeError: 'DataFrame' object has no attribute 'to_json'

In [5]:
for i in als_df:
    for j in i.recommendations:
        print(i.userId, j.propertyId,j.rating)

TypeError: Column is not iterable